## Imports

In [2]:
from geopy.geocoders import GoogleV3
from bs4 import BeautifulSoup
import requests
import time
import pandas as pd
import numpy as np
import urllib3
import re
from textwrap import shorten
import os

In [3]:
# df = pd.read_csv('2022 Chicago Broker Ranking - FINAL - Raw Data.csv')

## Image URL collector

In [4]:
# Drop last n rows of a df. In case there are sums that need clipped
# df.drop(df.tail(n).index, inplace=True)

In [5]:
# df['image_links'] = ''
# links = []
# for url in df['story_link']:
#     try:
#         page = requests.get(url)
#         soup = BeautifulSoup(page.content, 'html.parser')
#         images = soup.find_all('img')
#         counter = 0
#         for image in images:
#             counter += 1
#             if 'jpg' in image['src']:
#                 links.append(image['src'])
#                 if counter == len(images):
#                     links.append('no image found')
#                 break
#     except:
#         links.append('no_image')

# df['image_links'] = links

## Article link formatter

In [6]:
# len(links)

In [7]:
# df["short_description"] = df["full_address"].apply(lambda s: shorten(s, width=20, placeholder=""))
# df['remaining_desc'] = df.apply(lambda row : row['full_address'].replace(str(row['short_description']), ''), axis=1)
# df['remaining_desc']

# df["description_link"] = '<a href="' + df["story_link"] + '" target="_blank" rel="noopener noreferrer">' + df["short_description"] + "</a>" + df["remaining_desc"]
# df['description_link']

In [8]:
# df.columns

In [9]:
# df['full_address'] = df['ADDRESS'] + ' ' + df['CITY'] + ' ' + df['STATE OR PROVINCE']

In [10]:
# df = df.dropna(subset='Final Agent/Team')

In [11]:
# len(df.full_address)

## Google Maps API Geolocater Setup

In [12]:
# %store -r google_maps_API_Key
# geolocator = GoogleV3(api_key=google_maps_API_Key)

In [13]:
# df['geo_address'] = df['full_address']
# df['loc'] = df['geo_address'].apply(geolocator.geocode, timeout=10)
# df['point'] = df['loc'].apply(lambda loc: tuple(loc.point) if loc else None)
# df[['lat','lon','altitude']] = pd.DataFrame(df['point'].to_list(),index=df.index)

In [14]:
df = pd.read_csv('chicago_broker_rankings_august_2020_with_geo_points.csv')

## Correction Section

## HTML popup formatter

In [15]:
df.columns

Index(['Unnamed: 0', 'MLS#', 'Unique', 'Final Agent/Team', 'agent_type',
       'TRD Notes', 'PROPERTY TYPE', 'ADDRESS', 'CITY', 'STATE OR PROVINCE',
       'ZIP OR POSTAL CODE', 'SOLD DATE', 'PRICE', 'URL', 'full_address',
       'geo_address', 'loc', 'point', 'lat', 'lon', 'altitude'],
      dtype='object')

In [24]:
def popup_html(row):
    i = row
    address = df['full_address'].iloc[i]
    team = df['Final Agent/Team'].iloc[i]
    date_sold = df['SOLD DATE'].iloc[i]
    price = df['PRICE'].iloc[i]
    agent_type = df['agent_type'].iloc[i]
    
    html = '''<!DOCTYPE html>
    <html>
    <head>
    <h4>{}</h4>'''.format(address) + '''
    </head>
    <body>
    <strong>Team:</strong> {}'''.format(team) + '''<br> 
    <strong>Date sold:</strong> {}'''.format(date_sold) + '''<br>
    <strong>Price:</strong> {}'''.format(price) + '''<br>
    <strong>Type:</strong> {}'''.format(agent_type) + '''<br>
    </body>
    </html>
    '''
    return html


### HTML reservoir

In [17]:
#     Developer(s): <strong><em>{}'''.format(developer) + '''</strong></em><br><br>

## Map Maker

In [27]:
import folium
from folium.plugins import MarkerCluster
import branca

f = folium.Figure(width=750, height=750)
m = folium.Map(location=df[["lat", "lon"]].mean().to_list(),zoom_start=8)

title_html = '''
              <h4 align="center" style="font-size:16px"><b>{}</b></h4>
             '''.format(f'Top Chicago Broker Sales - August 2022')

marker_cluster = MarkerCluster().add_to(m)

for i in range(0,len(df)):
    html = popup_html(i)
    iframe = branca.element.IFrame(html=html, width=510,height=280)
    popup = folium.Popup(folium.Html(html, script=True), max_width=510)
    folium.Marker([df['lat'].iloc[i],df['lon'].iloc[i]],
                 popup=popup).add_to(marker_cluster)

m.get_root().html.add_child(folium.Element(title_html))
m.fit_bounds(bounds=df[['lat','lon']].mean().to_list(),max_zoom=15)
# m.add_to(f)
m

In [19]:
m.save('index.html')

## Map URL snagger

Map template URL: `https://trd-digital.github.io/trd-news-interactive-maps/{map-folder-name}`

In [20]:
base_name = 'https://trd-digital.github.io/trd-news-interactive-maps/'

In [21]:
cwd = os.getcwd()

cwd = cwd.split('/')

final_name = base_name + cwd[-1]
print(final_name)

https://trd-digital.github.io/trd-news-interactive-maps/Chicago_broker_rankings_08_2022
